# **Finding Recoded Stop Codons Using Long ORF Coverage**


In [17]:
import numpy as np

We first generate the reverse complement of a DNA sequence, which is necessary for analyzing the reverse strands in ORF detection.
  - **Line 2:** Define a dictionary `complement` that maps each nucleotide to its complement.
    - Adenine (A) complements Thymine (T), etc.
  - **Lines 4-11:** Create the reverse complement sequence.
    - **Line 5:** Initialize an empty list `rev_comp` to store complement bases.
    - **Line 7:** Reverse the input squence using `reversed(seq)` and iterate over each base.
    - **Line 9:** For each base, use `complement.get(base, 'N')` to find its complement. If the base is not in the dictionary, default to N.
    - **Line 10:** Join the complement base to the `rev_comp` list.
    - **Line 12:** Join the list of complement bases into a string using `''.join(rev_comp)` and return it as the reverse complement sequence.

In [18]:
def reverse_complement(seq):
    complement = {'A': 'T', 'T': 'A', 'G': 'C', 'C': 'G', 'N': 'N'}
    rev_comp = []
    for base in reversed(seq):
        comp_base = complement.get(base, 'N')
        rev_comp.append(comp_base)
    return ''.join(rev_comp)

Then we calculate the fraction of the DNA sequence covered by long ORFs (length ≥ `min_orf_length`) across all six reading frames (three forward and three reverse).
  - **Line 9:** Iterate over each reading frame.
  - **Line 10:** Offset the sequence according to the frame using `seq[frame:]`.
  - **Line 12:** Generate codons by slicing the sequence every three nucleotides.
  - **Lines 13-30:** Identify ORFs and mark coverage.
    - **Loop Logic:**
      - **Lines 15-28:** While iterating over codons:
        - **Line 17:** If a stop codon is encountered:
          - **Lines 19-24:** Calculate ORF length and check if it meets the minimum length.
          - **Lines 21-23:** If it does, mark the positions in `coverage` array.
        - **Line 25:** Update `start` to begin after the stop codon.
        - **Line 26:** Increment `i` to move to the next codon.
    - **Lines 29-33:** After the loop, check for an ORF that reaches the end of the sequence without a stop codon and mark coverage if it meets the minimum length.
- **Processing the Reverse Strand:**
  - **Line 36:** Obtain the reverse complement of the sequence using `reverse_complement(seq)`.
  - **Lines 37-59:** Similar logic is applied to the reversse strand.
    - **Note on Position Mapping:**
      - Since we're working on the reverse strand, positions need to be mapped back to the original sequence coordinates.
      - **Line 47:** Calculate `orf_start_pos` and `orf_end_pos` by subtracting from `seq_length`.
      - **Line 49:** Use `min` and `max` to ensure the correct range in the coverage array.
- **Calculating Coverage Fraction:**
  - **Line 62:** Sum the values in `coverage` to get the total number of positions covered by long ORFs.
  - **Line 63:** Divide by `seq_length` to obtain the coverage fraction.



In [19]:
def get_long_orf_coverage(seq, stop_codons, min_orf_length=600):
    seq_length = len(seq)
    coverage = [0] * seq_length
    
    frames = [0, 1, 2]

    for frame in frames:
        frame_seq = seq[frame:] 
        # Generate list of codons in this frame
        codons = [frame_seq[i:i+3] for i in range(0, len(frame_seq)-2, 3)]
        start = 0  # Start index of the current ORF
        i = 0      # Codon index
        while i < len(codons):
            codon = codons[i]
            if codon in stop_codons:
                # Calculate ORF length in nucleotides
                orf_length = (i - start) * 3
                if orf_length >= min_orf_length:
                    # Mark the positions covered by this ORF
                    orf_start_pos = frame + start * 3
                    orf_end_pos = frame + i * 3
                    for pos in range(orf_start_pos, min(orf_end_pos, seq_length)):
                        coverage[pos] = 1
                start = i + 1  # Start a new ORF after the stop codon
            i += 1
        # Check for an ORF that reaches the end without a stop codon
        orf_length = (i - start) * 3
        if orf_length >= min_orf_length:
            orf_start_pos = frame + start * 3
            orf_end_pos = seq_length  # End of sequence
            for pos in range(orf_start_pos, orf_end_pos):
                coverage[pos] = 1

    rev_seq = reverse_complement(seq)
    for frame in frames:
        frame_seq = rev_seq[frame:]  # Sequence offset by the frame
        codons = [frame_seq[i:i+3] for i in range(0, len(frame_seq)-2, 3)]
        start = 0
        i = 0
        while i < len(codons):
            codon = codons[i]
            if codon in stop_codons:
                orf_length = (i - start) * 3
                if orf_length >= min_orf_length:
                    # Map positions back to the original sequence
                    orf_start_pos = seq_length - (frame + i * 3)
                    orf_end_pos = seq_length - (frame + start * 3)
                    for pos in range(min(orf_start_pos, orf_end_pos), max(orf_start_pos, orf_end_pos)):
                        if 0 <= pos < seq_length:
                            coverage[pos] = 1
                start = i + 1
            i += 1
        # Check for an ORF that reaches the end without a stop codon
        orf_length = (i - start) * 3
        if orf_length >= min_orf_length:
            orf_start_pos = 0  # Start of sequence
            orf_end_pos = seq_length - (frame + start * 3)
            for pos in range(orf_start_pos, orf_end_pos):
                coverage[pos] = 1

    # Calculate coverage fraction
    total_covered = sum(coverage)
    coverage_fraction = total_covered / seq_length
    return coverage_fraction

## **Part 1: Negative Control Experiment**
We examine how varying GC content in random DNA sequences affects the likelihood of observing long ORFs purely by chance.
First, wwe generate a random DNA sequence with a specified length and GC content, simulating different geonmic compositions.
  - **Line 4:** Define the DNA bases.
  - **Lines 6-7:** Calculate the probabilities for AT and GC nucleotides.
    - Since there are two AT bases and two GC bases, we divide their respective probabilities by 2 to distribute evenly between them.
  - **Line 8:** Create a list `probs` with the probabilities in the order of `bases`.
  - **Line 10:** Use `np.random.choice` to generate a list of nucleotides:
    - `size=length` specifies the number of nucleotides to generate.
    - `p=probs` provides the probabilities for each nucleotide.
  - **Line 11:** Join the list of nucleotides into a single string to form the DNA sequence.

In [20]:
def generate_random_dna(length, gc_content):
    bases = ['A', 'T', 'G', 'C']
    at_prob = (1 - gc_content) / 2  
    gc_prob = gc_content / 2  
    probs = [at_prob, at_prob, gc_prob, gc_prob]
    sequence = ''.join(np.random.choice(bases, size=length, p=probs))
    return sequence

Now we find out how varying GC content affects the long ORF coverage in random DNA sequences, providing a negative control to compare against real genomes.
  - **Lines 2-4:** Initialize variables.
  - **Lines 6-13:** Loop over each GC content:
    - **Line 7:** Generate a random DNA sequence with the specified GC content.
    - **Line 8:** Define standard stop codons.
    - **Line 9:** Calculate the long ORF coverage using `get_long_orf_coverage`.
    - **Lines 11-12:** Append the results to the `results` list as a dictionary.
  - **Lines 15-18:** Print the results in a formatted table.
    - **Line 15:** Print the header with column names.
    - **Line 16:** Print a separator line.
    - **Lines 17-18:** Iterate over `results` and print each GC content and coverage value.
      - `"{:<12.0%}"` formats the GC content as a percentage with no decimals.
      - `"{:18.4f}"` formats the coverage as a floating-point number with four decimals.

In [21]:
def negative_control_experiment():
    gc_contents = [i / 100 for i in range(10, 91, 10)]  # GC content from 10% to 90%
    sequence_length = 100000  # Large enough to get stable statistics
    min_orf_length = 600      # ORFs of at least 600 nucleotides (200 amino acids)

    results = []

    for gc in gc_contents:
        seq = generate_random_dna(sequence_length, gc)
        stop_codons_standard = ['TAA', 'TAG', 'TGA']
        coverage = get_long_orf_coverage(seq, stop_codons_standard, min_orf_length)

        results.append({
            'gc_content': gc,
            'coverage': coverage
        })

    print("{:<12s}{:>18s}".format('GC Content', 'Long ORF Coverage'))
    print('-' * 30)
    for result in results:
        print("{:<12.0%}{:18.4f}".format(
            result['gc_content'],
            result['coverage']
        ))

    return results

negative_control_experiment()

GC Content   Long ORF Coverage
------------------------------
10%                     0.0000
20%                     0.0000
30%                     0.0000
40%                     0.0000
50%                     0.0061
60%                     0.0969
70%                     0.3362
80%                     0.9849
90%                     1.0000


[{'gc_content': 0.1, 'coverage': 0.0},
 {'gc_content': 0.2, 'coverage': 0.0},
 {'gc_content': 0.3, 'coverage': 0.0},
 {'gc_content': 0.4, 'coverage': 0.0},
 {'gc_content': 0.5, 'coverage': 0.00606},
 {'gc_content': 0.6, 'coverage': 0.09685},
 {'gc_content': 0.7, 'coverage': 0.33619},
 {'gc_content': 0.8, 'coverage': 0.98492},
 {'gc_content': 0.9, 'coverage': 1.0}]

- **Low GC Content (10% - 50%):**
  - Long ORF coverage is effectively zero.
  - Stop codons are frequent due to the high AT content, preventing the formation of long ORFs.
- **Moderate GC Content (60%):**
  - Slight increase in long ORF coverage (~4%).
  - Fewer stop codons occur by chance, allowing some longer ORFs.
- **High GC Content (70% - 90%):**
  - Significant increase in long ORF coverage.
  - At 80% GC content, almost the entire sequence is covered by long ORFs.
  - At 90% GC content, the coverage reaches 100%.

**Impact of Stop Codon Frequency:**

- **Stop codons (TAA, TAG, TGA) are AT-rich. In sequences with high AT content, stop codons occur more frequently by chance**:  
  Stop codons contain either two or three AT nucleotides, making them highly prone to appearing in sequences with a high percentage of AT bases. In low GC content sequences, the stop codons occur frequently by random chance. This frequent appearance of stop codons prematurely terminates potential ORFs, leading to very short ORFs and minimal ORF coverage.

- **High GC content reduces the probability of random stop codons, allowing longer ORFs to form without interruption**:  
  As GC content increases, the likelihood of encountering stop codons (which are composed of AT bases) decreases significanlty. This reduction in the frequency of stop codons leads to fewer interruptions in sequences that might otherwise form long ORFs. With fewer random stop codons in the sequence, ORFs can extend further without being cut short by a stop signal, leading to much higher ORF coverage. This is why ORF coverage rises sharply in high GC content genomes, as sequences with more GC pairs are least likely to be interrupted by stop codons and can therefore maintain longer ORFs.

## **Part 2: Analysis of Phage Genomes**

Now it's time to analyze actual phage genomes to identify those that may be using recoded stop codons (TAG or TGA) by examining changes in long ORF covarage under different genetic codes.

We read a DNA sequence from a FASTA file, concatenating all sequence lines while ignoring header and empty lines.

  - **Line 2:** Initialize an empty string `sequence`.
  - **Line 3:** Open the file in read mode using a context manager (`with` statement).
  - **Lines 4-9:** Iterate over each line in the file:
    - **Line 5:** Remove leading and trailing whitespace using `line.strip()`.
    - **Line 6:** Skip empty lines.
    - **Line 7:** Skip header lines that start with '>'.
    - **Line 9:** Append the sequence line to `sequence`, converting it to uppercase to ensure consistency.

In [22]:
def read_fasta_sequence(filename):
    sequence = ''
    with open(filename, 'r') as file:
        for line in file:
            line = line.strip()
            if not line:
                continue 
            if line.startswith('>'):
                continue
            sequence += line.upper()
    return sequence

Next step is to analyze each phage genome to calculate long ORF coverage under different genetic codes and identifies potential recoded phages based on simgificant increases in coverage.

  - **Lines 5-29:** Loop over each genome file:
    - **Line 6:** Read the genome sequence using `read_fasta_sequence`.
    - **Line 7:** Extract the genome name by splitting the filename at the period and taking the first part.
    - **Lines 10-12:** Define stop codon lists for different genetic codes.
      - **Standard Genetic Code:** All three stop codons are stops.
      - **TAG Recoded:** Only TAA and TGA are stops; TAG is a sense codon.
      - **TGA Recoded:** Only TAA and TAG are stops; TGA is a sense codon.
    - **Lines 15-17:** Calculate long ORF coverage using the `get_long_orf_coverage` function for each genetic code.
    - **Lines 20-21:** Calculate the ratios of coverage when a stop codon is recoded to the coverage under the standard genetic code.
    - **Lines 24-28:** Store the results in the `results` list as a dictionary.
  - **Lines 31-36:** Print the results in a formatted table.
    - **Line 32:** Define the header with column names.
    - **Line 33:** Print a separator line.
    - **Lines 35-36:** Iterate over `results` and print the values for each genome.
  - **Lines 38-42:** Identify and print phages likely to be recoded based on the coverage ratios.
    - A threshold of 1.2 is used to consider a significant increase in coverage.

In [23]:
def analyze_phage_genomes():
    genome_files = [
        'arugula.fa', 'basil.fa', 'chickpea.fa', 'gooseberry.fa',
        'huckleberry.fa', 'juniper.fa', 'lentil.fa', 'quince.fa',
        'sage.fa', 'tangerine.fa'
    ]

    results = []

    for genome_file in genome_files:
        seq = read_fasta_sequence(genome_file)
        genome_name = genome_file.split('.')[0]  # Extract genome name

        # Define stop codons for different genetic codes
        stop_codons_standard = ['TAA', 'TAG', 'TGA']
        stop_codons_tag_recoded = ['TAA', 'TGA']
        stop_codons_tga_recoded = ['TAA', 'TAG'] 

        # Calculate coverage with standard genetic code
        coverage_standard = get_long_orf_coverage(seq, stop_codons_standard)

        # Calculate coverage with TAG recoded
        coverage_tag_recoded = get_long_orf_coverage(seq, stop_codons_tag_recoded)

        # Calculate coverage with TGA recoded
        coverage_tga_recoded = get_long_orf_coverage(seq, stop_codons_tga_recoded)

        ratio_tag = coverage_tag_recoded / coverage_standard
        ratio_tga = coverage_tga_recoded / coverage_standard

        results.append({
            'genome': genome_name,
            'coverage_standard': coverage_standard,
            'coverage_tag_recoded': coverage_tag_recoded,
            'coverage_tga_recoded': coverage_tga_recoded,
            'ratio_tag': ratio_tag,
            'ratio_tga': ratio_tga
        })

    header = "{:<12s} {:>15s} {:>18s} {:>18s} {:>18s} {:>18s}".format(
        'Genome', 'Coverage Std', 'Coverage TAG Rec', 'Coverage TGA Rec',
        'Ratio TAG/Std', 'Ratio TGA/Std')
    print(header)
    print('-' * len(header))

    for result in results:
        print("{:<12s} {:15.4f} {:18.4f} {:18.4f} {:18.4f} {:18.4f}".format(
            result['genome'],
            result['coverage_standard'],
            result['coverage_tag_recoded'],
            result['coverage_tga_recoded'],
            result['ratio_tag'],
            result['ratio_tga']
        ))

    # Identify recoded phages
    print("\nIdentifying recoded phages:")
    for result in results:
        if result['ratio_tag'] > 1.2:
            print(f"{result['genome']} is likely TAG-recoded.")
        if result['ratio_tga'] > 1.2:
            print(f"{result['genome']} is likely TGA-recoded.")

analyze_phage_genomes()

Genome          Coverage Std   Coverage TAG Rec   Coverage TGA Rec      Ratio TAG/Std      Ratio TGA/Std
--------------------------------------------------------------------------------------------------------
arugula               0.3724             0.3913             0.6935             1.0506             1.8620
basil                 0.7609             0.7945             0.7854             1.0442             1.0323
chickpea              0.7770             0.7902             0.7786             1.0170             1.0021
gooseberry            0.2827             0.7673             0.3165             2.7139             1.1194
huckleberry           0.7574             0.7862             0.7803             1.0379             1.0302
juniper               0.2765             0.7380             0.2968             2.6689             1.0734
lentil                0.3646             0.3798             0.6995             1.0416             1.9184
quince                0.7740             0.8045        

- **Phages with a high ratio of TAG coverage to standard coverage (>1.2):**
  - **gooseberry**: Ratio TAG/Std = 2.7139
  - **juniper**: Ratio TAG/Std = 2.6689

  These two phages show a dramatic increase in ORF coverage when TAG is recoded as a sense codon. This perhaps suggests that these phages are likely using a genetic code where TAG is recoded as a sense codon, allowing ORFs to extend through TAG stop codons, leading to significantly longer ORFs and higher coverage.

- **Phages with a high ratio of TGA coverage to standard coverage (>1.2):**
  - **arugula**: Ratio TGA/Std = 1.8620
  - **lentil**: Ratio TGA/Std = 1.9184

  These two phages show a large increase in ORF covarage when TGA is recoded as a sense codon, suggesting that these phages likely use a genetic code where TGA is recoded as a sense codon. This recoding allows ORFs to extend through TGA stop codons, similarly leading to longer ORFs and increased coverage.

- **Phages with ratios close to 1.0:**
  - **basil**, **chickpea**, **huckleberry**, **quince**, **sage**, **tangerine**

  The remaining phages show only a slight increase in ORF coverage when either TAG or TGA is recoded, with ratios close to 1. This suggests that these phages likely use the standard genetic code and are not recoding either TAG or TGA as sense codons. ORFs in these genomes terminate at the standard stop codons, and recoding does not lead to any significant extension of ORFs.

### **Conclusion:**

Through my analysis, I have successfully identified four phages—**gooseberry**, **juniper**, **arugula**, and **lentil**—that are highly likely to utilize recoded stop codons. This conclusion is based on the significant increases in long ORF coverage observed when either **TAG** or **TGA** is recoded as a sense codon in these genomes. The pronounced jumps in ORF coverage ratios strongly suggest that these phages have evolved alternative genetic codes, where stop codons conventionally used for translation termination are instead re-purposed to encode amino acids, allowing their coding regions to reach beyond the boundaries set by the standard genetic code. This finding reinforcess the hypothesis that long ORF coverage can serve as a reliable computational method for detecting phages with recoded stop codons.

On the other hand, the remaining phages—**basil**, **chickpea**, **huckleberry**, **quince**, **sage**, and **tangerine**—appear to adhere to the standard genetic code. In these genomes, ORF coverage remains largely unchanged even when TAG or TGA was recoded as a sense codon. Minimal changes in coverage ratios indicate that stop codons in these phages function as expected, terminating translation and limiting the length of ORFs. This suggests that these phages do not employ alternative genetic codes, and their genomic architectures aligns with the traditional interpretation of stop codons as signals for the end of translation.